# doubledot.Salesforce
> Salesforce class for transfering data from Vantix to Salesforce

In [97]:
#| default_exp crema_sf

In [98]:
%load_ext autoreload
%autoreload 2

In [99]:
#| exporti 
import io
from nbdev.showdoc import *
import requests
import json
import jmespath as jp
import re
from time import sleep
from fastcore.basics import patch
import fileinput
import pandas as pd
import os
from doubledot.ATMS_api import ATMS_api as ATMS
import time

## Salesforce @property sf_access_token @staticmethod list_files

In [100]:
#| export
## Module for Salesforce API

class Salesforce:
    """Class for Salesforce API"""
    class_download_dir = os.path.join(os.getcwd(),'sf_download')
    class_upload_dir = os.path.join(os.getcwd(),'sf_upload')
    transfer_lock = False # lock to prevent multiple transfers at once - not implemented yet. but probably necessary to work with withh nbdev_test 

    ## Salesforce table relationships 
    ## these are also orderd by dependency
    model_d = {     'Contact'               :{ 'lookups_d': dict(), 'external_id':'contactId__c'},
                    'Membership__c'         :{ 'lookups_d': dict(), 'external_id':'membershipId__c'},
                    'MembershipTerm__c'     :{ 'lookups_d': {'membershipKey__c': 'Membership__c'}, 'external_id':'membershipTermId__c'},
                    'MembershipMember__c'   :{ 'lookups_d': {'contactKey__c': 'Contact', 'membershipTermKey__c': 'MembershipTerm__c' }, 'external_id':'membershipMemberId__c'},
                    # in SF change saleId__c to saleId__c
                    'Sale__c'               :{ 'lookups_d': {'booking_contactKey__c': 'Contact'}, 'external_id':'saleId__c'},
                    # in SF change membershipTermKey__c to membershipTermKey__c
                    'SaleDetail__c'         :{ 'lookups_d': {'membershipTermKey__c':'MembershipTerm__c', 'saleId__c': 'Sale__c'}, 'external_id':'saleDetailId__c'},
                    # in SF change tickeKey__c to ticketId__c
                    # change saleId__c to saleKey__c in Ticket__c
                    'Ticket__c'             :{ 'lookups_d': {'saleKey__c': 'Sale__c', 'saleDetailKey__c': 'SaleDetail__c'}, 'external_id':'ticketId__c'} 
            }

    def __init__(self):
        # set up access token 
        self._sf_access_token = self.get_token_with_REST()
        self.bulk_job_id = None
        self._atms = None

        # create unique download directory per instance
        if not os.path.exists(Salesforce.class_download_dir):
            os.makedirs(Salesforce.class_download_dir)
            print(f"Directory 'atms_download' created successfully.")
        else:
            print(f"Directory 'atms_download' already exists.")


    @property
    def sf_access_token(
        self 
     ) -> str : #the access toke
        """a @property
        retrieve token for Salesforce - verifies that token is still valid and attempts to get a new one from Salesforce site if not
        """
        if not(self.test_token()):
            self._sf_access_token = self.get_token_with_REST()
            # check to see if getting token worked
            assert (self.sf_access_token), "Fetching new token didn't fix problem"
        return self._sf_access_token


    @property
    def atms( self):
        if not self._atms:
            self._atms = ATMS()
        return self._atms
    
    @staticmethod
    def list_files():
        return os.listdir(Salesforce.class_download_dir)

show_doc(Salesforce.sf_access_token)


   

---

[source](https://github.com/josephsmann/doubledot/blob/master/doubledot/crema_sf.py#L60){target="_blank" style="float:right; font-size:smaller"}

### Salesforce.sf_access_token

>      Salesforce.sf_access_token ()

a @property
retrieve token for Salesforce - verifies that token is still valid and attempts to get a new one from Salesforce site if not

## get_token_with_REST

In [101]:
#| export
@patch
def get_token_with_REST(self: Salesforce):
    """retieve the access token from Salesforce

    Returns:
        string: the access token 
    """
    with open('secrets.json') as f:
        secrets = json.load(f)
    
    DOMAIN = secrets['instance']
    payload = {
        'grant_type': 'password',
        'client_id': secrets['client_id'],
        'client_secret': secrets['client_secret'],
        'username': secrets['username'],
        'password': secrets['password'] + secrets['security_token']
    }
    oauth_url = f'{DOMAIN}/services/oauth2/token'

    auth_response = requests.post(oauth_url, data=payload)
    return auth_response.json().get('access_token') ######## <<<<<<<<<<<<<<<< .       



## test_token

In [102]:
#| export
@patch
def test_token(self: Salesforce):
    """Verify that token is still valid. If it isn't, it attempts to get a new one.

    Returns:
        boolean: true if token is valid, false otherwise
    """
    sf_headers = { 'Authorization': f"Bearer {self._sf_access_token}", 'Content-Type': 'application/json' }
    end_point ="https://cremaconsulting-dev-ed.develop.my.salesforce.com"
    service = "/services/data/v57.0/"
    r = requests.request("GET", end_point+service+f"limits", headers=sf_headers, data={})
    valid_token = r.status_code == 200
    if not(valid_token): print(r.status_code, type(r.status_code))
    return valid_token
    


## create_job

In [103]:
#| export
@patch
def create_job(self: Salesforce, 
                sf_object: str ='Contact', # the Salesforce object were going to operate on. 
                operation: str ='insert', # the database operation to use. Can be "insert","upsert" or "delete"
                external_id: str = 'External_Id__c' # when using "upsert", this field is used to identify the record
                )-> requests.Response :
    """Get job_id from Salesforce Bulk API

    """
    # Args: 
    #     sf_object (str, optional): the Salesforce object were going to operate on. Defaults to 'Contact'.
    #     operation (str, optional): ∆. Defaults to 'insert'.
    #     external_id (str, optional): the external id field for upsert operations. Defaults to 'External_Id__c'.
    #     sf_object (str, optional): the Salesforce object were going to operate on. Defaults to 'Contact'.
    #     operation (str, optional): the operation that will be used against the object. Defaults to 'insert'.
    #     external_id (str, optional): the external id field for upsert operations. Defaults to 'External_Id__c'.
    #     contentType (str, optional): the content type of the file. Defaults to 'CSV', 'JSON' also accepted.
    # Returns: 
    #     response: a response object containg the job_id. For more information on the response object see https://www.w3schools.com/python/ref_requests_response.asp
    #     a response object see https://www.w3schools.com/python/ref_requests_response.asp
        
    # Salesforce API docs: https://developer.salesforce.com/docs/atlas.en-us.api_asynch.meta/api_asynch/create_job.htm    
    url = "https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest"

    # https://developer.salesforce.com/docs/atlas.en-us.api_asynch.meta/api_asynch/datafiles_prepare_csv.htm
    ## we can set columnDelimiter to `,^,|,;,<tab>, and the default <comma>
    # sets the object to Contact, the content type to CSV, and the operation to insert
    payload_d = {
        "object": sf_object,
        "contentType": "CSV",
        # set columnDelimiter to TAB instead of comma for ease of dealing with commas in address fields
        #https://developer.salesforce.com/docs/atlas.en-us.api_asynch.meta/api_asynch/create_job.htm
        "columnDelimiter": "TAB", 
        "operation": operation
    }
    
    # as per https://developer.salesforce.com/docs/atlas.en-us.api_asynch.meta/api_asynch/walkthrough_upsert.htm
    if operation=='upsert':
        payload_d['externalIdFieldName']=external_id
    payload = json.dumps(payload_d)
    
    headers = {
    'Content-Type': 'application/json',
    'Authorization': f'Bearer {self.sf_access_token}'
    }

    response = requests.request("POST", url, headers=headers, data=payload)
    # print(response.text)
    try:
        self.bulk_job_id = response.json()['id']
    except TypeError:
        print("Bad response in Salesforce.create_job :\n", response.text)
        
    print(f"Created job {self.bulk_job_id} for {sf_object} with operation {operation}") 
    return response 


## upload_csv

In [104]:
#| export
@patch
def upload_csv(self : Salesforce, 
                obj_s: str = "", # Salesforce object to upload 
                # num_rows: int = 100, # the number of rows to upload 
                ) -> requests.Response:
    """Using the job_id from the previous step, upload the csv file to the job

    Args:
        file (filepointer): file pointer to the csv filek
    """
    # if not(file):
    #     # throw error
    #     assert False, "File not found"


    assert obj_s in ['Contact', 'Membership__c', 'MembershipTerm__c', 'MembershipMember__c', 'Sale__c', 'Ticket__c', 'SaleDetail__c']

    print(f"Uploading job {self.bulk_job_id} of object {obj_s}")

    # file_path_s = os.path.join(Salesforce.class_download_dir , f"{obj_s}.csv")
    file_path_s = os.path.join(Salesforce.class_upload_dir , f"{obj_s}.csv")

    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest/{self.bulk_job_id}/batches"

    # replace all occurrences of '\2019' with \'
    # we may have done this in ATMS already, but just in case
    try:
        for line in fileinput.input(files=file_path_s, inplace=True):
            line = line.replace('\u2019', "'")
            print(line, end='') # this prints to the file instead of stdout (!!)

        with open(file_path_s,'r') as payload:
            headers = {
                'Content-Type': 'text/csv',
                'Authorization': f'Bearer {self.sf_access_token}'
                }
            response = requests.request("PUT", url, headers=headers, data=payload)
    except FileNotFoundError:
        print("File not found error in Saleforce.upload_csv: ", file_path_s)
        return None
    
    return response
   

## close_job

In [105]:
#| export 
@patch
def close_job(self: Salesforce):
    # close the job (from Postman)
    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest/{self.bulk_job_id}"

    payload = json.dumps({
        "state": "UploadComplete"
    })
    headers = {
    'Content-Type': 'application/json',
    'Authorization': f'Bearer {self.sf_access_token}'
    }

    response = requests.request("PATCH", url, headers=headers, data=payload)

    # print(response.text)
    return response.json()
     

## job_status

In [106]:
#| export       
# get job status (from Postman)
@patch
def job_status(self: Salesforce):
    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest/{self.bulk_job_id}"

    payload = {}
    headers = {
    'Authorization': f'Bearer {self.sf_access_token}'
    }
    response = requests.request("GET", url, headers=headers, data=payload)
    return response.json()



## successful_results

In [107]:
#| export
@patch
def successful_results(self : Salesforce):
    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest/{self.bulk_job_id}/successfulResults"

    payload = {}
    headers = {
        'Authorization': f'Bearer {self.sf_access_token}'
    }

    response = requests.request("GET", url, headers=headers, data=payload)
    
    return response


## failed_result

In [108]:
#| export
@patch
def failed_results(self: Salesforce):
    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/jobs/ingest/{self.bulk_job_id}/failedResults"

    payload = {}
    headers = {
        'Authorization': f'Bearer {self.sf_access_token}'
    }

    response = requests.request("GET", url, headers=headers, data=payload)

    # 
    return response


## get_sf_object_ids

In [109]:
#| export
@patch
def get_sf_object_ids(self: Salesforce, 
                      object: str = 'Contact' # REST endpoint for data object
                      ):
    """Get Safesforce IDs for a the specified object

    """
    print(f"Retrieving Object Ids for {object} from Salesforce")
    sf_headers = { 'Authorization': f"Bearer {self.sf_access_token}", 'Content-Type': 'application/json' }
    end_point ="https://cremaconsulting-dev-ed.develop.my.salesforce.com"
    service = "/services/data/v57.0/"
    r = requests.request("GET", end_point+service+f"query/?q=SELECT+Id+FROM+{object}", headers=sf_headers, data={})
    assert isinstance(r.json(), dict), f"response: {r.json()}, header: {sf_headers}"
    object_ids = [d.get('Id') for d in r.json()['records']]
    while r.json()['done'] == False:
        new_url = end_point+r.json()['nextRecordsUrl']
        print(new_url)
        r = requests.request("GET", new_url, headers=sf_headers, data={})
        print((r.json()))
        fresh_object_ids = [d.get('Id') for d in r.json()['records']]
        print(len(fresh_object_ids))   
        object_ids+=fresh_object_ids
        
    print('total number of objects = ',len(object_ids))
    return object_ids


## delete_sf_objects

In [110]:
#| export
@patch
def delete_sf_objects(self: Salesforce, 
                      obj_s: str = 'Contact'
                      ):
    """Delete Salesforce objects"""
    # assert False, "want to catch test calls to this function"
    print(f"Deleting {obj_s} objects from Salesforce")
    object_ids = self.get_sf_object_ids(obj_s)
    file_path_s = os.path.join(Salesforce.class_download_dir , f"{obj_s}.csv")
    print(f"In Salesforce.delete_sf_objects: Deleting {len(object_ids)} {obj_s} objects using {file_path_s}")
    with open(file_path_s, 'w') as f:
        f.write('Id\n')
        for id in object_ids:
            f.write(id+'\n')
            
    # force execute_job to use the csv file we just created        
    self.execute_job(obj_s, 'delete', use_ATMS_data=False)
        


## test_sf_object_load_and_delete

In [111]:
#| export
@patch
def test_sf_object_load_and_delete(self: Salesforce, 
        sf_object_s : str = None, # Salesforce API endpoint
        input_file_s: str = None, # local file name
        remove_sf_objs: bool = False # remove the data just added to Salesforce
        ):
    """Test loading a Salesforce object with data from a local file"""
    assert sf_object_s
    assert input_file_s
    assert False, "This function hasn't been maintained"

    # sf.create_job('MembershipMembers__c', contentType='CSV')
    self.create_job(sf_object_s, contentType='CSV')
    print("Salesforce job id: ", self.bulk_job_id)

    #replace 
    # culprit is \u2019 - it cannot be encoded in latin-1 codec
    self.upload_csv(input_file_s)
    
        

    self.close_job()
    self.failed_results()
    self.successful_results()
    self.job_status()

    if remove_sf_objs:
        self.delete_sf_objects('membershipTerm__c')

In [112]:
#| export
def escape_quotes(text):
    # Escape single quotes
    # text = re.sub(r"\'", r"\\'", text)
    text = re.sub(r"\'", r"_", text)
    # Escape double quotes
    text = re.sub(r'\"', r'_', text)
    # text = re.sub(r',', r'*', text) ## shouldn't be necessary with tab delimiter
    # text = re.sub(r'\"', r'\\"', text)
    return text.strip()

## process_memberships

In [136]:
#| export

 #### modify so parent fields use correct shit 
#### maybe use a spreadsheet to make life easier 
# Name,Mother_Of_Child__r.contactId
# CustomObject1,123456

mem_s = "[].{membershipId__c: membershipId, \
    memberSince__c: memberSince, \
    updateDate__c: updateDate}"

memTerm_s = "[].membershipTerms[].{membershipTermId__c: membershipTermId,\
membershipKey__r_1_membershipId__c:membershipKey,\
effectiveDate__c:effectiveDate,\
expiryDate__c:expiryDate,\
membershipType__c:membershipType,\
upgradeFromTermKey__c:upgradeFromTermKey,\
giftMembership__c:giftMembership,\
refunded__c:refunded,\
saleDetailKey__c:saleDetailKey,\
itemKey__c:itemKey}"

memMembers_s = "[].membershipTerms[].membershipMembers[].{membershipMemberId__c:membershipMemberId,\
membershipTermKey__r_1_membershipTermId__c:membershipTermKey,\
cardNumber__c:cardNumber,\
membershipNumber__c:membershipNumber,\
cardStatus__c:cardStatus,\
contactKey__r_1_contactId__c:contactKey,\
displayName__c:displayName}"

@patch
def process_memberships(self: Salesforce ):
    """Unpack memberships data from atms object and write to membership, membership_terms, and membership_members csv files.
    
    We could modify this function to only process one of Memmbership, MembershipTerm, or MembershipMember.
    """
    # print("Processing memberships data")
    # custom objects need '__c' suffix
    mem_d = { 'memberships': {'fname':'Membership__c.csv', 'jmespath': mem_s},
               'membership_terms': {'fname':'MembershipTerm__c.csv','jmespath': memTerm_s},
               'membership_members': {'fname': 'MembershipMember__c.csv', 'jmespath': memMembers_s}
                }
            

    if not ('memberships' in self.atms.obj_d):
        self.atms.load_data_file_to_dict('memberships')
        assert 'memberships' in self.atms.obj_d, f"memberships not in atms.obj_d {self.atms.obj_d.keys()}"
    
    atms_d = self.atms.obj_d['memberships']

    for key, v_pair in mem_d.items():
        file_path_s = os.path.join(Salesforce.class_download_dir, v_pair['fname'])
        dict_l = jp.search(v_pair['jmespath'], atms_d)
        # print(f"Salesforce: Writing {len(dict_l)} {key} objects to {file_path_s}")
        with open(file_path_s, 'w') as f:
            if len(dict_l) == 0:
                # print(f"Warning: no {key} objects found")
                continue
            # hack to create header with a dot in it, jmespath won't do it
            f.write('\t'.join([s.replace('_1_','.') for s in dict_l[0].keys()]) + '\n') # header
            for d in dict_l:
                #changed this to not write None for empty values, eg "" for null and false (a default value)
                f.write('\t'.join([str(v) if v else "" for v in d.values()]) + '\n')
    

## process_sales

In [114]:
#| export


@patch
def process_sales(self: Salesforce ):
    search_s = "[].{saleId__c : saleKey,\
            saleAmount__c : saleAmount,\
            paymentAmount__c : paymentAmount,\
            saleDate__c : saleDate,\
            active__c : active,\
            terminalKey__c : terminalKey,\
            booking_bookingId__c   : booking.bookingId,\
            booking_bookingContactKey__c : booking.bookingContactKey,\
            booking_contactKey__r_1_contactId__c : booking.contactKey,\
            booking_contactIndividualKey__c : booking.contactIndividualKey,\
            booking_contactOrganizationKey__c : booking.contactOrganizationKey,\
            booking_displayName__c : booking.displayName,\
            booking_firstName__c : booking.firstName,\
            booking_lastName__c : booking.lastName,\
            booking_email__c : booking.email,\
            booking_phone__c : booking.phone}"
            # eventDate__c : eventDate,\
            # booking_contactKey__c : booking_contactKey,\
    
    assert 'sales' in self.atms.obj_d, f"sales not in atms.obj_d {self.atms.obj_d.keys()}"
    dict_l = jp.search(search_s, self.atms.obj_d['sales'])

    file_path_s = os.path.join(Salesforce.class_download_dir, 'Sale__c.csv')

    # print(f"Salesforce: Writing {len(dict_l)} 'Sales' objects to {file_path_s}")
    columnDelimiter = '\t'
    with open(file_path_s, 'w') as f:
        # hack to create header with a dot in it, jmespath won't do it
        header = '\t'.join([s.replace('_1_','.') for s in dict_l[0].keys()])
        f.write(header + '\n') # header
        for item in dict_l:
            # changed this from single space to empty string if null
            l = [escape_quotes(str(v)) if v else "" for v in item.values()]
            f.write(columnDelimiter.join(l)+'\n')


        

## process_tickets



In [115]:
#| export


@patch
def process_tickets(self: Salesforce ):
    search_s = "[].tickets[].{ticketId__c : ticketKey,\
        saleKey__r_1_saleId__c : saleKey,\
        saleDetailKey__r_1_saleDetailId__c : saleDetailKey,\
        itemDescription__c : itemDescription,\
        ticketDisplay__c : ticketDisplay}"
        # scheduleDate__c : scheduleDate,\
        # scheduleEndDate__c : scheduleEndDate,\

    assert 'sales' in self.atms.obj_d, f"sales not in atms.obj_d {self.atms.obj_d.keys()}"
    dict_l = jp.search(search_s, self.atms.obj_d['sales'])

    file_path_s = os.path.join(Salesforce.class_download_dir, 'Ticket__c.csv')

    # print(f"Salesforce: Writing {len(dict_l)} 'Ticket' objects to {file_path_s}")
    columnDelimiter = '\t'
    with open(file_path_s, 'w') as f:
        # hack to create header with a dot in it, jmespath won't do it
        header = '\t'.join([s.replace('_1_','.') for s in dict_l[0].keys()])
        f.write(header + '\n') # header
        for item in dict_l:
            # changed this from single space to empty string if null
            l = [escape_quotes(str(v)) if v else "" for v in item.values()]
            f.write(columnDelimiter.join(l)+'\n')


        

## process_saleDetails

In [116]:
#| export


@patch
def process_saleDetails(self: Salesforce ):
    search_s = "[].saleDetails[].{\
        saleDetailId__c : saleDetailId,\
        itemKey__c : itemKey,\
        scheduleKey__c : scheduleKey,\
        rateKey__c : rateKey,\
        categoryKey__c : categoryKey,\
        itemCategory__c : itemCategory,\
        pricingPriceKey__c : pricingPriceKey,\
        itemPrice__c : itemPrice,\
        itemTotal__c : itemTotal,\
        couponTotal__c : couponTotal,\
        discountTotal__c : discountTotal,\
        total__c : total,\
        revenueDate__c : revenueDate,\
        refundReason__c : refundReason,\
        refundReasonKey__c : refundReasonKey,\
        systemPriceOverride__c : systemPriceOverride,\
        membershipTermKey__r_1_membershipTermId__c : membershipTermKey,\
        saleId__r_1_saleId__c : saleId}" 
    
    assert 'sales' in self.atms.obj_d, f"sales not in atms.obj_d {self.atms.obj_d.keys()}"
    dict_l = jp.search(search_s, self.atms.obj_d['sales'])

    file_path_s = os.path.join(Salesforce.class_download_dir, 'SaleDetail__c.csv')

    # print(f"Salesforce: Writing {len(dict_l)} 'SaleDetail' objects to {file_path_s}")
    columnDelimiter = '\t'
    with open(file_path_s, 'w') as f:
        # hack to create header with a dot in it, jmespath won't do it
        header = '\t'.join([s.replace('_1_','.') for s in dict_l[0].keys()])
        f.write(header + '\n') # header
        for item in dict_l:
            # changed this from single space to empty string if null
            l = [escape_quotes(str(v)) if v else "" for v in item.values()]
            f.write(columnDelimiter.join(l)+'\n')


        

## process_contacts

In [124]:
#| export
search_s = "[].{LastName: lastName,\
    FirstName: firstName,\
    MailingPostalCode: addresses[0].postalZipCode,\
    MailingCity: addresses[0].city,\
    MailingStreet: addresses[0].line1, \
    MailingCountry: addresses[0].country, \
    Phone: phones[?phoneType == 'Business'].phoneNumber | [0],\
    Email: emails[0].address[0],\
    contactId__c: contactId}"

import re



@patch
def process_contacts(self: Salesforce ):
    """ unpack contacts data from atms object and write to contacts csv file."""
    # print("process_contacts")
    if not ('contacts' in self.atms.obj_d):
        self.atms.load_data_file_to_dict('contacts')
        assert 'contacts' in self.atms.obj_d, f"contacts not in atms.obj_d {self.atms.obj_d.keys()}"
    
    file_path_s = os.path.join(Salesforce.class_download_dir, 'Contact.csv')
    dict_l = jp.search(search_s, self.atms.obj_d['contacts'])

    # if contact record has no LastName then
    for r in dict_l:
        if r['LastName'] == None:
            r['LastName'] = 'Not Provided'

    # print(f"Salesforce: Writing {len(dict_l)} 'Contact' objects to {file_path_s}")
    columnDelimiter = '\t'
    with open(file_path_s, 'w') as f:
        header = columnDelimiter.join(dict_l[0].keys())
        f.write(header+'\n')
        for item in dict_l:
            l = [escape_quotes(str(v)) if v else " " for v in item.values()]
            f.write(columnDelimiter.join(l)+'\n')

## process_objects


In [125]:
#| export
@patch
def process_objects(self: Salesforce,
                    sf_object_s: str = "",
                    use_ATMS_data: bool = True
                    ):

    valid_obj_l = ['Contact', 'Membership__c', 'MembershipTerm__c', 'MembershipMember__c', 'Sale__c', 'Ticket__c','SaleDetail__c']
    if sf_object_s not in valid_obj_l:
        print(f"sf_object_s must be one of {', '.join(valid_obj_l)}")
        return
        
    print("Salesforce.process_objects: sf_object_s :",sf_object_s)

    if sf_object_s == 'SaleDetail__c' and use_ATMS_data:
        # this creates a file Sales__c.csv in the class_download_dir
        self.process_saleDetails()

    if sf_object_s == 'Ticket__c' and use_ATMS_data:
        # this creates a file Sales__c.csv in the class_download_dir
        self.process_tickets()

    if sf_object_s == 'Sale__c' and use_ATMS_data:
        # this creates a file Sales__c.csv in the class_download_dir
        self.process_sales()
    
    if sf_object_s == 'Contact' and use_ATMS_data:
        # this creates a file Contact.csv in the class_download_dir
        self.process_contacts()
    
    if sf_object_s in ['Membership__c', 'MembershipMember__c', 'MembershipTerm__c'] and use_ATMS_data:
        # this creates files Membership__c.csv, MembershipMember__c.csv, MembershipTerm__c.csv in the class_download_dir
        self.process_memberships()

## execute_job

In [126]:
#| export

@patch
def execute_job(self: Salesforce, 
        sf_object_s : str = None, # Salesforce API object name
        operation : str = None, # REST operation, e.g. insert, upsert, delete
        max_trys : int = 20, # max number of times to try to get job status
        external_id : str = 'External_Id__c', # name of the field that is the unique identifier to ATMS
        use_ATMS_data : bool = True, # if True, update SF data directly from ATMS data, otherwise use previous data
        # **kwargs : dict # additional parameters to pass to the REST API
        ):
    """Test loading a Salesforce object with data from a local file"""
    print("execute_job")
    

    ## translate dictionaries to csv files
    self.process_objects(sf_object_s=sf_object_s, use_ATMS_data=use_ATMS_data)

    ## start data transfer to Salesforce server
    self.create_job(sf_object=sf_object_s, operation=operation, external_id=external_id)
    self.upload_csv(sf_object_s)
    self.close_job()

    counter = 0
    sleep_time = 3
    
    job_status = self.job_status()['state']
    print("job status:", self.job_status()['state'])

    while job_status !='JobComplete' and job_status !='Failed' and counter < max_trys:
        print(f"waiting for job to complete, try {counter}, status: {self.job_status()['state']}")
        counter += 1
        time.sleep(sleep_time)
        job_status = self.job_status()['state']

    print("Failed results:")
    print(self.failed_results().text)

## get_fields from Salesforce for an object 

In [127]:
#| export
@patch
def get_fields(self:Salesforce, 
               obj:str # the name of the Salesforce object
               ) -> requests.Response:
    """Get the fields for a given Salesforce object"""
    sf_headers = { 'Authorization': f"Bearer {sf._sf_access_token}", 'Content-Type': 'application/json' }
    url = f"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v57.0/sobjects/{obj}/describe"
    # print(url)
    response = requests.request("GET", url, headers=sf_headers)
    print(response)
    r = response.json()
    if response.status_code == 200:
        r = response.json()
        names = jp.search("fields[].name",r)
        return names
    else:
        raise Exception(f"Error: {response.status_code} {response.reason}")

In [128]:
#| eval: false

## Perfect Data 

In [129]:
# pelton_ids = [ 4708, 119430, 119431, 144164,144165, 144166, 144167 ]
# # put data into atms_downloads
# for obj in ['sales', 'contacts', 'memberships']:
#     # does this not get written to file?, no. it does not. and we don't want it to because we're working on proccessing rn.
#     sf.atms.fetch_data_by_contactIds(obj, pelton_ids) 

# # write data to json files
# sf.atms.write_data_to_json_files()


## `retreive_atms_records_by_contactId`

In [130]:
#| export

@patch
def retreive_atms_records_by_contactId(
    self: Salesforce, # the Salesforce object
    contactId_l : list # list of contactIds to retrieve
    ):
    """Retreive ATMS records for a list of contactIds and write them to json files"""
    for obj in ['sales', 'contacts', 'memberships']:
        # does this not get written to file?, no. it does not. and we don't want it to because we're working on proccessing rn.
        sf.atms.fetch_data_by_contactIds(obj, contactId_l) 

    # write data to json files
    sf.atms.write_data_to_json_files()

## Test `retreive_atms_records_by_contactId`

In [131]:
#| eval: false
sf = Salesforce()
pelton_ids = [ 4708, 119430, 119431, 144164,144165, 144166, 144167 ]
sf.retreive_atms_records_by_contactId(pelton_ids)

# number of objects in dictionary
assert len(sf.atms.obj_d) == len(['sales', 'contacts', 'memberships','items']), f"wrong number of objects in dictionary {sf.atms.obj_d.keys()}"
# number of files in directory
assert len(os.listdir(sf.atms.download_dir)) == len(['sales', 'contacts', 'memberships','items']), f"wrong number of files in directory {sf.atms.download_dir}"



Directory 'atms_download' already exists.
Directory 'atms_download' already exists.
my id is ekd9yp9v
144164
we have contact_id 144164 and obj is sales
http://crm-api-telus.atmsplus.com/api/sales/contact/144164
[{'saleKey': '310928', 'saleAmount': '123.0500', 'paymentAmount': '123.0500', 'saleDate': '2005-08-19T10:23:33.03', 'active': True, 'terminalKey': 4, 'ticketCount': 0, 'eventDate': None, 'booking': {'bookingId': 48112, 'bookingContactKey': 192717, 'bookingContactType': 'Primary     ', 'contactKey': 144164, 'contactIndividualKey': 137810, 'contactOrganizationKey': 5649, 'displayName': 'Pelton, Donna', 'firstName': 'Donna', 'lastName': 'Pelton', 'email': 'tdpelton@shaw.ca', 'phone': '7804592956'}, 'saleComment': None, 'saleDetails': [{'saleDetailId': 760379, 'saleId': 310928, 'itemKey': 7, 'scheduleKey': None, 'rateKey': 3, 'categoryKey': None, 'itemQuantity': 1, 'pricingPriceKey': 207, 'itemPrice': 105.0, 'itemTotal': 105.0, 'couponTotal': 0.0, 'discountTotal': 0.0, 'total': 123.

In [132]:
def remove_duplicates(file_path : str, idx: str = None):
    df = pd.read_csv('sf_download/'+file_path, sep='\t').drop_duplicates(subset=idx)
    df.to_csv('sf_download/'+file_path+'2',sep='\t', index=False)
    return df

def has_duplicates(file_s: str, idx: str = None):
    df = pd.read_csv('sf_download/'+file_s, sep='\t')
    return (df.shape)[0] != (df.drop_duplicates( subset=idx).shape)[0]

## generate upload files

In [133]:
#| export
## this will have only contacts that are members, and only members that are contacts. 
## is possible to have duplicates if a contact is a member of more than one membership?
## yes but the duplicated fields will only be in one group or the other
## so we separate them and then reduce them
## but we should really just make a function for this...

## given two dataframes and two fields return two dataframes that are subsets of the original dataframes for which the two fields match
def match_df(df1, df2, field1, field2):
    df1 = df1[df1[field1].isin(df2[field2])]
    df2 = df2[df2[field2].isin(df1[field1])]
    return df1, df2


In [137]:
# test that all external ids are unique
# test that all lookups are valid

def test_lookup_fields(df_d):
    for fromKey in Salesforce.model_d.keys():
        # verify that external id is unique
        assert df_d[fromKey][Salesforce.model_d[fromKey]['external_id']].is_unique, f"external id not unique for {fromKey}"

        # verify that all lookups are valid 
        r_cols = [col for col in df_d[fromKey].columns if re.search('__r\.', col)]
        for col in r_cols:
            col_matches = re.search('(.*)__r\.(.*)', col)
            fromField = col
            lookupField = col_matches.group(1)+'__c'
            toField = col_matches.group(2)
            parentTable = Salesforce.model_d[fromKey]['lookups_d'][lookupField]
            fromColumn = df_d[fromKey][fromField]
            toColumn = df_d[parentTable][toField]
            assert (fromColumn.isin(toColumn)).all(), f"bad lookup: {fromKey} {fromField} {toField}"


## Filter on externalId that are pointed to

In [165]:
    
## these funcs all use the global variable df_d

# function that returns all the fields that point to a given foreign key
def fields_pointing_to_foreign_key(foreign_key):
    return_list = []
    for name, df in df_d.items():
        for col in df.columns:
            if re.search(foreign_key, col) and  len(col)>len(foreign_key):
                return_list.append((name, col))
    return return_list

# function that takes a foreign key and returns a set of all value that point to it
def get_pointing_foreign_key_values(foreign_key):
    return_set = set()
    table_cols_l = fields_pointing_to_foreign_key(foreign_key)
    for table, col in table_cols_l:
        return_set.update(set(df_d[table][col]))
    return return_set


# df2_d should be a dictionary of perfect dataframes
df2_d = {}
for k, v in Salesforce.model_d.items():
    foreign_key = v['external_id']
    if len(fields_pointing_to_foreign_key(foreign_key)) == 0:
        df2_d[k] = df_d[k]
        print(k, len(df_d[k]), len(df2_d[k]))
        continue
    point_to_foreign_key = get_pointing_foreign_key_values(foreign_key)
    # print(k, s) 
    keep_b = df_d[k][foreign_key].isin(point_to_foreign_key)
    df2_d[k] = df_d[k][keep_b]
    print(k, len(df_d[k]), len(df2_d[k]))


    ## so why is this happening? eg. in Ticket__c nobody points it (or do they)

Contact 7 7
Membership__c 4 4
MembershipTerm__c 24 7
MembershipMember__c 11 11
Sale__c 82 5
SaleDetail__c 16 10
Ticket__c 10 10


In [150]:
# try to do the same thing but using dataframes

# collect all external_ids and their corresponding tables
external_id_d = {}
for name, model in Salesforce.model_d.items():
    external_id_d[name] = model['external_id']
    # external_id_l.append(model['external_id'])

# for each of the collected external_ids, find the corresponding table and column that point at them
_d = {}
for table, external_id in external_id_d.items():
    _d[(table, external_id)] = []
    for k,df in df_d.items():
        cols = df.columns
        for col in cols:
            if re.search(external_id, col) and len(col) > len(external_id):
                print(f"{k} : {col}\n points to \n{table} : {external_id} \n")
                _d[(table, external_id)].append((k, col),)
                



MembershipMember__c : contactKey__r.contactId__c
 points to 
Contact : contactId__c 

Sale__c : booking_contactKey__r.contactId__c
 points to 
Contact : contactId__c 

MembershipTerm__c : membershipKey__r.membershipId__c
 points to 
Membership__c : membershipId__c 

MembershipMember__c : membershipTermKey__r.membershipTermId__c
 points to 
MembershipTerm__c : membershipTermId__c 

SaleDetail__c : membershipTermKey__r.membershipTermId__c
 points to 
MembershipTerm__c : membershipTermId__c 

SaleDetail__c : saleId__r.saleId__c
 points to 
Sale__c : saleId__c 

Ticket__c : saleKey__r.saleId__c
 points to 
Sale__c : saleId__c 

Ticket__c : saleDetailKey__r.saleDetailId__c
 points to 
SaleDetail__c : saleDetailId__c 



In [141]:

    # verify that external_id is pointed to by a lookup
    ## for every external_id, find every lookup field that points to it, make dictionary of external_id:[lookup_field]
    external_id_l = []
    for name, model in Salesforce.model_d.items():
        external_id_l.append(model['external_id'])
    
    # find all lookup fields that point to external_id
    for external_id in external_id_l:
        for name, model in Salesforce.model_d.items():
            for lookup_field in model['lookups_d'].keys():
                lookup_column = df_d[name][lookup_field]
                if lookup_column.isin(external_id).any():
                    print(f"lookup field {lookup_field} in {name} points to {external_id}")
                    continue
    



KeyError: 'membershipKey__c'

In [138]:
# starting from atms object dictionary, create a dictionary of dataframes for all SF objects
# using this dictionary df_d, we can then remove duplicates of rows with same external_id
# and remove any row which has a lookup to a non-existent foreign key

assert len(sf.atms.obj_d) == 4, 'atms dictionaries not available'
obj_l = Salesforce.model_d.keys()
for obj in obj_l:
    # write atms dictionaries to csv file, if dictionary there - otherwise exception
    sf.process_objects(obj)

# create a dictionary of dataframes for all SF objects  
df_d = {}
for i in Salesforce.model_d.keys(): 
    df_d[i] = pd.read_csv('sf_download/'+i+'.csv', sep='\t')
try:
    print("this should fail")
    test_lookup_fields(df_d)    
except:
    print("and it did. good.")
    
for i in Salesforce.model_d.keys(): 
    # remove duplicates of rows with same external_id
    print("dropping duplicates for ", i, " on ", sf.model_d[i]['external_id'],"...")
    df_d[i].drop_duplicates(subset= Salesforce.model_d[i]['external_id'], inplace=True)

# remove any row which has a lookup to a non-existent foreign key
for obj,relations in sf.model_d.items():
    print(obj)
    for fromField, parent in relations['lookups_d'].items():
        parentExternalId = Salesforce.model_d[parent]['external_id']
        toColumn = df_d[parent][parentExternalId]

        # combine from field and parent external id to get Salesforce lookup field
        newFromField = fromField[:-1]+'r.'+parentExternalId
        fromColumn = df_d[obj][newFromField]
        indGood_b = fromColumn.isin(toColumn)
        good_b = indGood_b.sum() == len(indGood_b)
        if not good_b:
            print('bad lookup: ', obj, newFromField, parentExternalId,len(indGood_b), len(indGood_b) - indGood_b.sum())
            df_d[obj]= match_df(df_d[obj], df_d[parent], newFromField, parentExternalId)[0]

try:
    print("this should NOT fail")
    test_lookup_fields(df_d)
except:
    print("but it did. Bad.")
    raise Exception("bad lookup")
finally:
    print("finally, it did not fail. Good.")

Salesforce.process_objects: sf_object_s : Contact
Salesforce.process_objects: sf_object_s : Membership__c
Salesforce.process_objects: sf_object_s : MembershipTerm__c
Salesforce.process_objects: sf_object_s : MembershipMember__c
Salesforce.process_objects: sf_object_s : Sale__c
Salesforce.process_objects: sf_object_s : SaleDetail__c
Salesforce.process_objects: sf_object_s : Ticket__c
this should fail
and it did. good.
dropping duplicates for  Contact  on  contactId__c ...
dropping duplicates for  Membership__c  on  membershipId__c ...
dropping duplicates for  MembershipTerm__c  on  membershipTermId__c ...
dropping duplicates for  MembershipMember__c  on  membershipMemberId__c ...
dropping duplicates for  Sale__c  on  saleId__c ...
dropping duplicates for  SaleDetail__c  on  saleDetailId__c ...
dropping duplicates for  Ticket__c  on  ticketId__c ...
Contact
Membership__c
MembershipTerm__c
MembershipMember__c
Sale__c
SaleDetail__c
bad lookup:  SaleDetail__c membershipTermKey__r.membership

In [85]:
df_d['SaleDetail__c'].columns

Index(['saleDetailId__c', 'itemKey__c', 'scheduleKey__c', 'rateKey__c',
       'categoryKey__c', 'itemCategory__c', 'pricingPriceKey__c',
       'itemPrice__c', 'itemTotal__c', 'couponTotal__c', 'discountTotal__c',
       'total__c', 'revenueDate__c', 'refundReason__c', 'refundReasonKey__c',
       'systemPriceOverride__c', 'membershipTermKey__r.membershipTermId__c',
       'saleId__r.saleId__c'],
      dtype='object')

In [75]:
## how do we test this?
for k, df in df_d.items():
    print(k, df.shape)
    assert df_d[k][Salesforce.model_d[k]['external_id']].is_unique, f"external id not unique in {k}"
    for obj,relations in sf.model_d.items():
    print(obj)
    for fromField, parent in relations['lookups_d'].items():
        parentExternalId = Salesforce.model_d[parent]['external_id']
        toColumn = df_d[parent][parentExternalId]

        # combine from field and parent external id to get Salesforce lookup field
        newFromField = fromField[:-1]+'r.'+parentExternalId
        fromColumn = df_d[obj][newFromField]
        indGood_b = fromColumn.isin(toColumn)
        good_b = indGood_b.sum() == len(indGood_b)
        if not good_b:
            print('bad lookup: ', obj, newFromField, parentExternalId,len(indGood_b), len(indGood_b) - indGood_b.sum())
            df_d[obj]= match_df(df_d[obj], df_d[parent], newFromField, parentExternalId)[0]

Contact (7, 9)
Membership__c (4, 3)
MembershipTerm__c (24, 10)
MembershipMember__c (11, 7)
Sale__c (82, 16)
SaleDetail__c (16, 18)
Ticket__c (10, 5)


In [ ]:
# generate csv files for each object
# using atms dictionaries if available 

# obj_l = ['Membership__c','MembershipTerm__c', 'MembershipMember__c', 'Sale__c', 'SaleDetail__c', 'Ticket__c', 'Contact']
obj_l = Salesforce.model_d.keys()
for obj in obj_l:
    # write atms dictionaries to csv file, if dictionary there - otherwise exception
    assert len(sf.atms.obj_d) == 4, 'atms dictionaries not available'
    sf.process_objects(obj)
    remove_duplicates(obj+'.csv', Salesforce.model_d[obj]['external_id'])
    assert has_duplicates(obj+'.csv2') == False, 'duplicates in '+obj
    try:
        os.remove('sf_download/'+obj+'.csv')
        print('removed '+obj+'.csv')
    except:
        print('no '+obj+'.csv')

sleep(20)
for obj in obj_l:
    os.rename('sf_download/'+obj+'.csv2', 'sf_download/'+obj+'.csv')

Salesforce.process_objects: sf_object_s : Contact
process_contacts
Salesforce: Writing 7 'Contact' objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Contact.csv
removed Contact.csv
Salesforce.process_objects: sf_object_s : Membership__c
Processing memberships data
Salesforce: Writing 11 memberships objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Membership__c.csv
Salesforce: Writing 56 membership_terms objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipTerm__c.csv
Salesforce: Writing 108 membership_members objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipMember__c.csv
removed Membership__c.csv
Salesforce.process_objects: sf_object_s : MembershipTerm__c
Processing memberships data
Salesforce: Writing 11 memberships objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Membership__c.csv
Salesforce: Writing 56 membership_terms objects to /Users/josephmann/Documents/Github/doubledot/

## working from top to here -

> currently Saleforce choking (Saturday morning 11:15 am 2023-05-20)
> still choking at 15:10 pm 2023-05-20

## Perfect Data
> perfect data - no duplicates, every external id is unique, every lookup has a corresponding record

In [ ]:
# """SaleDetail__c saleDetailId__c
# execute_job
# Created job 7508Y00000nHXnfQAG for SaleDetail__c with operation upsert
# Uploading job 7508Y00000nHXnfQAG of object SaleDetail__c
# job status: InProgress
# waiting for job to complete, try 0, status: InProgress
# Failed results:
# "sf__Id"	"sf__Error"	saleDetailId__c	itemKey__c	scheduleKey__c	rateKey__c	categoryKey__c	itemCategory__c	pricingPriceKey__c	itemPrice__c	itemTotal__c	couponTotal__c	discountTotal__c	total__c	revenueDate__c	refundReason__c	refundReasonKey__c	systemPriceOverride__c	MembershipTermKey__r.MembershipTermId__c	saleId__r.saleId__c
# ""	"INVALID_FIELD:Foreign key external ID: 310928 not found for field saleId__c in entity Sale__c:--"	"760379.0"	"7.0"	""	"3.0"	""	""	"207.0"	"105.0"	"105.0"	""	""	"123.05"	"2005-08-19"	""	""	"N"	""	"310928"
# ""	"INVALID_FIELD:Foreign key external ID: 75 not found for field saleId__c in entity Sale__c:--"	"199.0"	"30.0"	"119.0"	"1.0"	"2.0"	""	"163.0"	"115.0"	"115.0"	""	"23.0"	"92.0"	"2001-07-03"	""	""	"N"	""	"75"
# ""	"INVALID_FIELD:Foreign key ex"""

## Generate Dictionary of SF Dataframes

In [ ]:
# create a dictionary of dataframes for all SF objects  
df_d = {}
for i in Salesforce.model_d.keys(): 
    df_d[i] = pd.read_csv('sf_download/'+i+'.csv', sep='\t')

## Verify Lookups 

In [71]:
### verify all lookup are satisfied using dataframes made from csv files

# after fixing SF, must recreate csv files AND df_d

from doubledot.crema_sf import match_df

# in words.. verify that all lookups exist in their parent tables
for obj,relations in sf.model_d.items():
    print(obj)
    for fromField, parent in relations['lookups_d'].items():
        parentExternalId = Salesforce.model_d[parent]['external_id']
        toColumn = df_d[parent][parentExternalId]

        # combine from field and parent external id to get Salesforce lookup field
        newFromField = fromField[:-1]+'r.'+parentExternalId
        fromColumn = df_d[obj][newFromField]
        indGood_b = fromColumn.isin(toColumn)
        good_b = indGood_b.sum() == len(indGood_b)
        if not good_b:
            print('bad lookup: ', obj, newFromField, parentExternalId,len(indGood_b), len(indGood_b) - indGood_b.sum())
            df_d[obj]= match_df(df_d[obj], df_d[parent], newFromField, parentExternalId)[0]




Contact
Membership__c
MembershipTerm__c
MembershipMember__c
Sale__c
SaleDetail__c
Ticket__c


## Write Perfect Data to `sf_upload` directory

In [ ]:
# write dictionary of dataframes to upload directory for all SF objects  
path = 'sf_upload/'
for k in Salesforce.model_d.keys(): 
    with open(path+k+'.csv', 'w') as f:
        f.write(df_d[k].to_csv(sep='\t', index=False))

## Write data to SF

## Write data from `sf_upload` to SF database 

In [ ]:


## upload all data to SF
for obj,relations in sf.model_d.items():
    print(obj, relations['external_id'] )
    sf.execute_job(obj, 'upsert', external_id=relations['external_id'], use_ATMS_data=False) 
    sleep(2)

Contact contactId__c
execute_job
Salesforce.process_objects: sf_object_s : Contact
Created job 7508Y00000nHvfkQAC for Contact with operation upsert
Uploading job 7508Y00000nHvfkQAC of object Contact
job status: JobComplete
waiting for job to complete, try 0, status: JobComplete
Failed results:
"sf__Id"	"sf__Error"	LastName	FirstName	MailingPostalCode	MailingCity	MailingStreet	MailingCountry	Phone	Email	contactId__c

Membership__c membershipId__c
execute_job
Salesforce.process_objects: sf_object_s : Membership__c
Created job 7508Y00000nHvfzQAC for Membership__c with operation upsert
Uploading job 7508Y00000nHvfzQAC of object Membership__c
job status: UploadComplete
waiting for job to complete, try 0, status: UploadComplete
Failed results:
"sf__Id"	"sf__Error"	membershipId__c	memberSince__c	updateDate__c

MembershipTerm__c membershipTermId__c
execute_job
Salesforce.process_objects: sf_object_s : MembershipTerm__c
Created job 7508Y00000nHvg4QAC for MembershipTerm__c with operation upsert


# Testing Stuff

In [25]:
sf = Salesforce()
# sf._sf_access_token

Directory 'atms_download' already exists.


In [26]:
sf.execute_job('MembershipMember__c', 'upsert', use_ATMS_data=False)


execute_job
Salesforce.process_objects: sf_object_s : MembershipMember__c
Bad response in Salesforce.create_job :
 [{"errorCode":"INVALIDJOB","message":"InvalidJob : Field name provided, External_Id__c does not match an External ID for MembershipMember__c"}]
Created job None for MembershipMember__c with operation upsert
Uploading job None of object MembershipMember__c


TypeError: list indices must be integers or slices, not str

In [ ]:
pelton_ids = [ 4708, 119430, 119431, 144164,144165, 144166, 144167 ]
sf.atms.fetch_data_by_contactIds('contacts', pelton_ids)
## we need data first
sf.process_contacts() # this has first and last names in it

144164
we have contact_id 144164 and obj is contacts
we have contact_id and obj is contacts
ATMS_api.get_telus_data :  http://crm-api-telus.atmsplus.com/api/contacts/144164
http://crm-api-telus.atmsplus.com/api/contacts/144164
{'contactId': 144164, 'contactType': 'Individual', 'username': None, 'createdDate': '2006-08-03T16:08:32.313', 'updateDate': '2006-08-03T16:08:32.313', 'emailOptIn': 'N', 'mailOptIn': 'N', 'phoneOptIn': 'N', 'contactIndividualKey': 137810, 'firstName': 'Donna', 'lastName': 'Pelton', 'middleName': None, 'birthDate': '0001-01-01T00:00:00', 'contactOrganizationKey': 0, 'organizationName': None, 'addresses': [{'addressId': 119705, 'contactKey': 144164, 'addressType': 'Home', 'line1': '96 Aspen Crescent', 'line2': None, 'line3': None, 'country': 'Canada', 'province': 'AB', 'county': None, 'city': 'St. Albert', 'postalZipCode': 'T8N 2L8   '}], 'alerts': [], 'contactTypes': [], 'emails': [{'emailId': 8052, 'contactKey': 144164, 'emailType': 'E-Mail', 'address': 'tdpelto

In [ ]:
pelton_ids = [ 4708, 119430, 119431, 144164,144165, 144166, 144167 ]
sf.atms.fetch_data_by_contactIds('sales', pelton_ids)
## we need data first
sf.process_sales() # this has first and last names in it

144164
we have contact_id 144164 and obj is sales
http://crm-api-telus.atmsplus.com/api/sales/contact/144164
[{'saleKey': '310928', 'saleAmount': '123.0500', 'paymentAmount': '123.0500', 'saleDate': '2005-08-19T10:23:33.03', 'active': True, 'terminalKey': 4, 'ticketCount': 0, 'eventDate': None, 'booking': {'bookingId': 48112, 'bookingContactKey': 192717, 'bookingContactType': 'Primary     ', 'contactKey': 144164, 'contactIndividualKey': 137810, 'contactOrganizationKey': 5649, 'displayName': 'Pelton, Donna', 'firstName': 'Donna', 'lastName': 'Pelton', 'email': 'tdpelton@shaw.ca', 'phone': '7804592956'}, 'saleComment': None, 'saleDetails': [{'saleDetailId': 760379, 'saleId': 310928, 'itemKey': 7, 'scheduleKey': None, 'rateKey': 3, 'categoryKey': None, 'itemQuantity': 1, 'pricingPriceKey': 207, 'itemPrice': 105.0, 'itemTotal': 105.0, 'couponTotal': 0.0, 'discountTotal': 0.0, 'total': 123.05, 'revenueDate': '2005-08-19T00:00:00', 'refundReasonKey': None, 'systemPriceOverride': 'N', 'member

In [149]:
sf.delete_sf_objects('Contact') 
sf.execute_job('Contact', 'insert', use_ATMS_data=True)

Deleting Contact objects from Salesforce
Retrieving Object Ids for Contact from Salesforce
total number of objects =  72
In Salesforce.delete_sf_objects: Deleting 72 Contact objects using /Users/josephmann/Documents/Github/doubledot/sf_download/Contact.csv
execute_job
Created job 7508Y00000nH37jQAC for Contact with operation delete
Uploading job 7508Y00000nH37jQAC of object Contact
job status: UploadComplete
waiting for job to complete, try 0, status: InProgress
Failed results:
"sf__Id"	"sf__Error"	Id
"0038Y00003bx8WPQAY"	"DELETE_FAILED:Your attempt to delete Ms. Rose Gonzalez could not be completed because it is associated with the following cases.: 00001000
:--"	"0038Y00003bx8WPQAY"
"0038Y00003bx8WQQAY"	"DELETE_FAILED:Your attempt to delete Mr. Sean Forbes could not be completed because it is associated with the following cases.: 00001017, 00001018
:--"	"0038Y00003bx8WQQAY"
"0038Y00003bx8WRQAY"	"DELETE_FAILED:Your attempt to delete Mr. Jack Rogers could not be completed because it is

In [182]:
_d = pd.read_csv(os.path.join(Salesforce.class_download_dir, 'Sale__c.csv'), sep='\t')
_d

saleKey__c  saleAmount__c  paymentAmount__c              saleDate__c   
0       310928         123.05            123.05   2005-08-19T10:23:33.03  \
1           75         184.00            184.00  2001-06-18T16:47:10.263   
2         6200           0.00              0.00  2001-07-16T08:16:37.513   
3        28717           0.00              0.00    2001-10-02T10:24:51.5   
4        34334           0.00              0.00  2001-10-27T19:08:29.763   
..         ...            ...               ...                      ...   
77     1615641           0.00              0.00  2017-12-19T13:21:29.843   
78     1615688           0.00              0.00   2017-12-19T15:15:33.23   
79     1776435           0.00              0.00  2019-03-20T11:53:35.733   
80      378568          98.32             98.32   2006-08-03T16:06:19.58   
81     1019680          55.65             55.65   2013-03-24T15:08:29.95   

    active__c  terminalKey__c  booking_bookingId__c   
0        True               4                   NaN  \
1        True               2                   NaN   
2        True              11                   NaN   
3        True               3                   NaN   
4        True              11                   NaN   
..        ...             ...                   ...   
77       True               1                   NaN   
78       True               1                   NaN   
79       True              99                   NaN   
80       True               2                   NaN   
81       True              15                   NaN   

    booking_bookingContactKey__c  booking_contactKey__r.External_Id__c   
0                            NaN                                   NaN  \
1                            NaN                                   NaN   
2                            NaN                                   NaN   
3                            NaN                                   NaN   
4                            NaN                                   NaN   
..                           ...                                   ...   
77                           NaN                                   NaN   
78                           NaN                                   NaN   
79                           NaN                                   NaN   
80                           NaN                                   NaN   
81                           NaN                                   NaN   

    booking_contactIndividualKey__c  booking_contactOrganizationKey__c   
0                               NaN                                NaN  \
1                               NaN                                NaN   
2                               NaN                                NaN   
3                               NaN                                NaN   
4                               NaN                                NaN   
..                              ...                                ...   
77                              NaN                                NaN   
78                              NaN                                NaN   
79                              NaN                                NaN   
80                              NaN                                NaN   
81                              NaN                                NaN   

    booking_displayName__c  booking_firstName__c  booking_lastName__c   
0                      NaN                   NaN                  NaN  \
1                      NaN                   NaN                  NaN   
2                      NaN                   NaN                  NaN   
3                      NaN                   NaN                  NaN   
4                      NaN                   NaN                  NaN   
..                     ...                   ...                  ...   
77                     NaN                   NaN                  NaN   
78                     NaN                   NaN                  Na

In [186]:
_d = sf.atms.obj_d['sales']
s = search_s = "[].{saleKey__c : saleKey,\
            saleAmount__c : saleAmount,\
            paymentAmount__c : paymentAmount,\
            saleDate__c : saleDate,\
            active__c : active,\
            terminalKey__c : terminalKey,\
            booking_bookingId__c   : booking.bookingId,\
            booking_bookingContactKey__c : booking.bookingContactKey,\
            booking_contactKey__r_1_External_Id__c : booking.contactKey,\
            booking_contactIndividualKey__c : booking.contactIndividualKey,\
            booking_contactOrganizationKey__c : booking.contactOrganizationKey,\
            booking_displayName__c : booking.displayName,\
            booking_firstName__c : booking.firstName,\
            booking_lastName__c : booking.lastName,\
            booking_email__c : booking.email,\
            booking_phone__c : booking.phone}"
jp.search(s, _d)

[{'saleKey__c': '310928',
  'saleAmount__c': '123.0500',
  'paymentAmount__c': '123.0500',
  'saleDate__c': '2005-08-19T10:23:33.03',
  'active__c': True,
  'terminalKey__c': 4,
  'booking_bookingId__c': 48112,
  'booking_bookingContactKey__c': 192717,
  'booking_contactKey__r_1_External_Id__c': 144164,
  'booking_contactIndividualKey__c': 137810,
  'booking_contactOrganizationKey__c': 5649,
  'booking_displayName__c': 'Pelton, Donna',
  'booking_firstName__c': 'Donna',
  'booking_lastName__c': 'Pelton',
  'booking_email__c': 'tdpelton@shaw.ca',
  'booking_phone__c': '7804592956'},
 {'saleKey__c': '75',
  'saleAmount__c': '184.0000',
  'paymentAmount__c': '184.0000',
  'saleDate__c': '2001-06-18T16:47:10.263',
  'active__c': True,
  'terminalKey__c': 2,
  'booking_bookingId__c': 71,
  'booking_bookingContactKey__c': 281,
  'booking_contactKey__r_1_External_Id__c': 4708,
  'booking_contactIndividualKey__c': 3,
  'booking_contactOrganizationKey__c': 0,
  'booking_displayName__c': 'Pelton

In [187]:
##### doesn't work because its not connecting to anything??

sf.delete_sf_objects('Sale__c') 
sf.execute_job('Sale__c', 'insert', use_ATMS_data=True, max_trys=10)

Deleting Sale__c objects from Salesforce
Retrieving Object Ids for Sale__c from Salesforce
total number of objects =  82
In Salesforce.delete_sf_objects: Deleting 82 Sale__c objects using /Users/josephmann/Documents/Github/doubledot/sf_download/Sale__c.csv
execute_job
Created job 7508Y00000nH44lQAC for Sale__c with operation delete
Uploading job 7508Y00000nH44lQAC of object Sale__c
job status: UploadComplete
waiting for job to complete, try 0, status: InProgress
waiting for job to complete, try 1, status: InProgress
Failed results:
"sf__Id"	"sf__Error"	Id

execute_job
Salesforce: Writing 82 'Sales' objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Sale__c.csv
Created job 7508Y00000nH3vBQAS for Sale__c with operation insert
Uploading job 7508Y00000nH3vBQAS of object Sale__c
job status: InProgress
waiting for job to complete, try 0, status: InProgress
waiting for job to complete, try 1, status: InProgress
Failed results:
"sf__Id"	"sf__Error"	saleKey__c	saleAmount__c	pay

In [162]:
print(sf.failed_results().text)

"sf__Id"	"sf__Error"	saleKey__c	saleAmount__c	paymentAmount__c	saleDate__c	active__c	terminalKey__c	eventDate__c	booking_bookingId__r.External_Id__c	booking_bookingContactKey__c	booking_bookingContactType__c	booking_contactKey__c	booking_contactIndividualKey__c	booking_contactOrganizationKey__c	booking_displayName__c	booking_firstName__c	booking_lastName__c	booking_email__c	booking_phone__c



In [145]:
sf.execute_job(sf_object_s='Contact', operation='upsert', use_ATMS_data=True, external_id='External_Id__c')

execute_job
process_contacts
Salesforce: Writing 7 'Contact' objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Contact.csv
Created job 7508Y00000nH31bQAC for Contact with operation upsert
Uploading job 7508Y00000nH31bQAC of object Contact
job status: InProgress
Failed results:
"sf__Id"	"sf__Error"	LastName	FirstName	MailingPostalCode	MailingCity	MailingStreet	MailingCountry	Phone	Email	External_Id__c



In [75]:
sf.get_fields('Contact')

<Response [200]>


['Id',
 'IsDeleted',
 'MasterRecordId',
 'AccountId',
 'LastName',
 'FirstName',
 'Salutation',
 'Name',
 'OtherStreet',
 'OtherCity',
 'OtherState',
 'OtherPostalCode',
 'OtherCountry',
 'OtherLatitude',
 'OtherLongitude',
 'OtherGeocodeAccuracy',
 'OtherAddress',
 'MailingStreet',
 'MailingCity',
 'MailingState',
 'MailingPostalCode',
 'MailingCountry',
 'MailingLatitude',
 'MailingLongitude',
 'MailingGeocodeAccuracy',
 'MailingAddress',
 'Phone',
 'Fax',
 'MobilePhone',
 'HomePhone',
 'OtherPhone',
 'AssistantPhone',
 'ReportsToId',
 'Email',
 'Title',
 'Department',
 'AssistantName',
 'LeadSource',
 'Birthdate',
 'Description',
 'OwnerId',
 'CreatedDate',
 'CreatedById',
 'LastModifiedDate',
 'LastModifiedById',
 'SystemModstamp',
 'LastActivityDate',
 'LastCURequestDate',
 'LastCUUpdateDate',
 'LastViewedDate',
 'LastReferencedDate',
 'EmailBouncedReason',
 'EmailBouncedDate',
 'IsEmailBounced',
 'PhotoUrl',
 'Jigsaw',
 'JigsawContactId',
 'CleanStatus',
 'IndividualId',
 'Level_

In [149]:
# sf.delete_sf_objects('Contact')
# sf.delete_sf_objects('Membership__c')
# sf.delete_sf_objects('MembershipTerm__c')
# sf.delete_sf_objects('MembershipMember__c')

atms = ATMS_api()
sf.atms = atms

Directory 'atms_download' already exists.
my id is vb4r9ypk


In [150]:
# sf.delete_sf_objects('Contact')

## Clean out SF database

In [151]:
# clean out SF database first
## this will stomp on any data in SF #### Please change !!!
# sf.delete_sf_objects('Contact')
# sf.delete_sf_objects('Membership__c')
# sf.delete_sf_objects('MembershipTerm__c')
# sf.delete_sf_objects('MembershipMember__c')


### Verify on Salesforce that the objects were deleted before proceeding
### None there ! 

Deleting Contact objects from Salesforce
Retrieving Object Ids for Contact from Salesforce
total number of objects =  15
In Salesforce.delete_sf_objects: Deleting 15 Contact objects using /Users/josephmann/Documents/Github/doubledot/sf_download/Contact.csv
execute_job
Created job 7508Y00000nGwMNQA0 for Contact with operation delete
Uploading job 7508Y00000nGwMNQA0 of object Contact
job status: InProgress


KeyboardInterrupt: 

In [ ]:
print(sf.get_sf_object_ids('Contact'))
print(sf.get_sf_object_ids('Membership__c'))
print(sf.get_sf_object_ids('MembershipTerm__c'))
print(sf.get_sf_object_ids('MembershipMember__c'))

Retrieving Object Ids for Contact from Salesforce
total number of objects =  15
['0038Y00003bx8WPQAY', '0038Y00003bx8WQQAY', '0038Y00003bx8WRQAY', '0038Y00003bx8WUQAY', '0038Y00003bx8WVQAY', '0038Y00003bx8WWQAY', '0038Y00003bx8WXQAY', '0038Y00003bx8WYQAY', '0038Y00003bx8WZQAY', '0038Y00003bx8WaQAI', '0038Y00003bx8WcQAI', '0038Y00003bx8WdQAI', '0038Y00003bx8WeQAI', '0038Y00003bx8WfQAI', '0038Y00003bx8WgQAI']
Retrieving Object Ids for Membership__c from Salesforce
total number of objects =  0
[]
Retrieving Object Ids for MembershipTerm__c from Salesforce
total number of objects =  0
[]
Retrieving Object Ids for MembershipMember__c from Salesforce
total number of objects =  0
[]


## Get fresh data

In [ ]:
atms.retrieve_and_clean('memberships', since_date='2004-05-01', max_rows=1000)
# atms.retrieve_and_clean('contacts', since_date='2020-01-01', max_rows=1000)
# atms.retrieve_and_clean('items', since_date='2020-01-01', max_rows=1000)

download dir is:  /Users/josephmann/Documents/Github/doubledot/atms_download/21ckdv53
resp_d = self.get_telus_data(memberships,offset=0, count= 1000, since_date=2004-05-01)
ATMS_api.get_telus_data: since_date is 2004-05-01
http://crm-api-telus.atmsplus.com/api/memberships/lastupdate?count=1000&offset=0&updateDate=2004-05-01
resp_d.keys():  dict_keys(['response', 'done'])
done: False, resp_d.json() : <Response [200]>
cleaning_data_file - download dir is:  /Users/josephmann/Documents/Github/doubledot/atms_download/21ckdv53
creating file:  /Users/josephmann/Documents/Github/doubledot/atms_download/21ckdv53/atms_transformed_memberships.json
Finished cleaning atms_memberships.json -> /Users/josephmann/Documents/Github/doubledot/atms_download/21ckdv53/atms_transformed_memberships.json
ATMS_api - Attempting to load:  /Users/josephmann/Documents/Github/doubledot/atms_download/21ckdv53/atms_transformed_memberships.json  into dict
ATMS_api: loaded 1000 memberships into dict


In [ ]:
jp.search("[]")

In [ ]:
atms.retrieve_and_clean('sales', since_date='2020-01-01', max_rows=100)


download dir is:  /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51
resp_d = self.get_telus_data(sales,offset=0, count= 100, since_date=2020-01-01)
ATMS_api.get_telus_data: since_date is 2020-01-01
http://crm-api-telus.atmsplus.com/api/sales/lastupdate?count=100&offset=0&updateDate=2020-01-01
resp_d.keys():  dict_keys(['response', 'done'])
done: False, resp_d.json() : <Response [200]>
cleaning_data_file - download dir is:  /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51
creating file:  /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51/atms_transformed_sales.json
Finished cleaning atms_sales.json -> /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51/atms_transformed_sales.json
ATMS_api - Attempting to load:  /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51/atms_transformed_sales.json  into dict
ATMS_api: loaded 100 sales into dict


In [ ]:
## put some data in csv files and try to make cheap SF Sales object
_d = sf.atms.obj_d['contacts']
# {key: _d[key] for key not in ['']}
# jp.search([].{})
# pd.DataFrame(_d)#.to_csv('Contact.csv', index=False, sep='\t')

In [ ]:
s ="""
[3].{contactId:type(contactId),
 contactType:type(contactType),
 username:type(username),
 createdDate:type(createdDate),
 updateDate:type(updateDate),
 emailOptIn:type(emailOptIn),
 mailOptIn:type(mailOptIn),
 phoneOptIn:type(phoneOptIn),
 contactIndividualKey:type(contactIndividualKey),
 firstName:type(firstName),
 lastName:type(lastName),
 middleName:type(middleName),
 birthDate:type(birthDate),
 contactOrganizationKey:type(contactOrganizationKey),
 organizationName:type(organizationName),
 addresses:type(addresses),
 alerts:type(alerts),
 contactTypes:type(contactTypes),
 emails:type(emails),
 phones:type(phones)
 }
"""



# jp.search("[].{abou: contactId}", _d[:4]),
# jp.search(s, _d[:4]),
# jp.search("[0].keys(@)", _d[:4])
# jp.search("[0].values(@)", _d[:4])
# jp.search("[0].{keys(@)}", _d[:4])
jp.search(s, _d)

jp.search("[*].*.{Name: , Type: type(@)}", _d[:4])





JMESPathTypeError: In function keys(), invalid type for value: 456268, expected one of: ['object'], received: "number"

In [ ]:
_d

[{'contactId': 456268,
  'contactType': 'Individual',
  'username': None,
  'createdDate': '2020-01-01T01:54:49.17',
  'updateDate': '2020-01-01T01:54:49.17',
  'emailOptIn': 'N',
  'mailOptIn': 'N',
  'phoneOptIn': 'N',
  'contactIndividualKey': 445732,
  'firstName': 'Naavneet',
  'lastName': 'Aulakh',
  'middleName': None,
  'birthDate': '0001-01-01T00:00:00',
  'contactOrganizationKey': 0,
  'organizationName': None,
  'addresses': [{'addressId': 396625,
    'contactKey': 456268,
    'addressType': 'Business',
    'line1': '112 Douglas Glen Pt. SE',
    'line2': None,
    'line3': None,
    'country': 'Canada',
    'province': 'AB',
    'county': None,
    'city': 'Calgary',
    'postalZipCode': 'T2Z 3G1             '}],
  'alerts': [],
  'contactTypes': [],
  'emails': [{'emailId': 262745,
    'contactKey': 456268,
    'emailType': 'E-Mail',
    'address': ['naavie90@gmail.com']}],
  'faxes': [],
  'phones': [{'phoneId': 579071,
    'contactKey': 456268,
    'phoneType': 'Business

In [ ]:
kk_d

{'contactId': 456268,
 'contactType': 'Individual',
 'username': None,
 'createdDate': '2020-01-01T01:54:49.17',
 'updateDate': '2020-01-01T01:54:49.17',
 'emailOptIn': 'N',
 'mailOptIn': 'N',
 'phoneOptIn': 'N',
 'contactIndividualKey': 445732,
 'firstName': 'Naavneet',
 'lastName': 'Aulakh',
 'middleName': None,
 'birthDate': '0001-01-01T00:00:00',
 'contactOrganizationKey': 0,
 'organizationName': None,
 'addresses': [{'addressId': 396625,
   'contactKey': 456268,
   'addressType': 'Business',
   'line1': '112 Douglas Glen Pt. SE',
   'line2': None,
   'line3': None,
   'country': 'Canada',
   'province': 'AB',
   'county': None,
   'city': 'Calgary',
   'postalZipCode': 'T2Z 3G1             '}],
 'alerts': [],
 'contactTypes': [],
 'emails': [{'emailId': 262745,
   'contactKey': 456268,
   'emailType': 'E-Mail',
   'address': ['naavie90@gmail.com']}],
 'faxes': [],
 'phones': [{'phoneId': 579071,
   'contactKey': 456268,
   'phoneType': 'Business',
   'phoneNumber': '5872150656',
 

## Put Data into Dataframes


In [ ]:
## try to see what how connected our daat is
dir = sf.class_download_dir
sf.process_contacts()
sf.process_memberships()
Contact_df = pd.read_csv(os.path.join(dir, 'Contact.csv'), sep='\t')
Membership_df = pd.read_csv(os.path.join(dir, 'Membership__c.csv'), sep='\t')
MembershipTerm_df = pd.read_csv(os.path.join(dir, 'MembershipTerm__c.csv'), sep='\t')
MembershipMember_df = pd.read_csv(os.path.join(dir, 'MembershipMember__c.csv'), sep='\t')

process_contacts
Salesforce: Writing 1000 'Contact' objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Contact.csv
Processing memberships data
Salesforce: Writing 1000 memberships objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Membership__c.csv
Salesforce: Writing 1211 membership_terms objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipTerm__c.csv
Salesforce: Writing 3986 membership_members objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipMember__c.csv


In [ ]:
for _df in [Contact_df, Membership_df, MembershipTerm_df, MembershipMember_df]:
    print(_df.shape, _df.columns)

(1000, 8) Index(['LastName', 'MailingPostalCode', 'MailingCity', 'MailingStreet',
       'MailingCountry', 'Phone', 'Email', 'External_Id__c'],
      dtype='object')
(1000, 3) Index(['membershipId__c', 'memberSince__c', 'updateDate__c'], dtype='object')
(1211, 10) Index(['membershipTermId__c', 'membershipKey__r.membershipId__c',
       'effectiveDate__c', 'expiryDate__c', 'membershipType__c',
       'upgradeFromTermKey__c', 'giftMembership__c', 'refunded__c',
       'saleDetailKey__c', 'itemKey__c'],
      dtype='object')
(3986, 7) Index(['membershipMemberId__c', 'membershipTermKey__r.membershipTermId__c',
       'cardNumber__c', 'membershipNumber__c', 'cardStatus__c',
       'contactKey__r.External_Id__c', 'displayName__c'],
      dtype='object')


In [200]:
display("""{mermaid}
graph TD;
    Membership-->MemberTerm;
    MemberTerm-->Member;
    Users-->Member;
    
""")

'{mermaid}\ngraph TD;\n    Membership-->MemberTerm;\n    MemberTerm-->Member;\n    Users-->Member;\n    \n'

```{mermaid}
graph TD;
    Membership-->MemberTerm;
    MemberTerm-->Member;
    Users-->Member;
    
```

## Find Data that is linked 

Duplicates seem to remain

In [ ]:
assert fContact_df['External_Id__c'].isin(fMembershipMember_df['contactKey__r.External_Id__c']).all()
assert fMembershipMember_df['contactKey__r.External_Id__c'].isin(fContact_df['External_Id__c']).all()

assert fMembershipMember_df['membershipTermKey__r.membershipTermId__c'].isin(fMembershipTerm_df['membershipTermId__c']).all()
assert fMembershipTerm_df['membershipTermId__c'].isin(fMembershipMember_df['membershipTermKey__r.membershipTermId__c']).all()

assert fMembershipTerm_df['membershipKey__r.membershipId__c'].isin(fMembership_df['membershipId__c']).all()
assert fMembership_df['membershipId__c'].isin(fMembershipTerm_df['membershipKey__r.membershipId__c']).all()



In [ ]:
for df in [fContact_df, fMembershipMember_df, fMembershipTerm_df, fMembership_df]:
    print(df.shape, df.columns)

(434, 8) Index(['LastName', 'MailingPostalCode', 'MailingCity', 'MailingStreet',
       'MailingCountry', 'Phone', 'Email', 'External_Id__c'],
      dtype='object')
(527, 7) Index(['membershipMemberId__c', 'membershipTermKey__r.membershipTermId__c',
       'cardNumber__c', 'membershipNumber__c', 'cardStatus__c',
       'contactKey__r.External_Id__c', 'displayName__c'],
      dtype='object')
(205, 10) Index(['membershipTermId__c', 'membershipKey__r.membershipId__c',
       'effectiveDate__c', 'expiryDate__c', 'membershipType__c',
       'upgradeFromTermKey__c', 'giftMembership__c', 'refunded__c',
       'saleDetailKey__c', 'itemKey__c'],
      dtype='object')
(171, 3) Index(['membershipId__c', 'memberSince__c', 'updateDate__c'], dtype='object')


## Write data to CSV

In [ ]:

fContact_df.to_csv(os.path.join(dir, 'Contact.csv'), index=False, sep='\t')
fMembership_df.to_csv(os.path.join(dir, 'Membership__c.csv'), index=False, sep='\t')
fMembershipTerm_df.to_csv(os.path.join(dir, 'MembershipTerm__c.csv'), index=False, sep='\t')
fMembershipMember_df.to_csv(os.path.join(dir, 'MembershipMember__c.csv'), index=False, sep='\t')

In [ ]:
# clean_Contact_df = Contact_df.merge(MembershipMember_df[['contactKey__r.External_Id__c']].drop_duplicates(), left_on='External_Id__c', right_on='contactKey__r.External_Id__c')
# clean_MembershipTerm_df = MembershipTerm_df.merge(MembershipMember_df[['membershipTermKey__r.membershipTermId__c']].drop_duplicates(), left_on='membershipTermId__c', right_on='membershipTermKey__r.membershipTermId__c')
# clean_MembershipTerm_df

In [ ]:
# # all the rows of MembershipMember_df that have a contactKey__r.External_Id__c that is in Contact_df
# merge_df = pd.merge(Contact_df, MembershipMember_df, how='inner', left_on='External_Id__c', right_on='contactKey__r.External_Id__c')
# print(merge_df.shape, merge_df.columns)

# # all the rows of merge_df that have a membershipTermKey__r.membershipTermId__c that is in MembershipTerm_df
# merge_df = pd.merge(merge_df, MembershipTerm_df, how='inner', left_on='membershipTermKey__r.membershipTermId__c', right_on='membershipTermId__c')
# print(merge_df.shape, merge_df.columns)

# # all the rows of merge_df that have a membershipTermKey__r.membershipTermId__c that is in membershipId__c
# merge_df = pd.merge(merge_df, Membership_df, how='inner', left_on='membershipKey__r.membershipId__c', right_on='membershipId__c')
# print(merge_df.shape, merge_df.columns)

In [ ]:
# how do I make csv files from merge_df (in 12 min)
# sweet_contacts_df = merge_df[ Contact_df.columns ]

# sweet_contacts_df.drop_duplicates(subset=['External_Id__c'], inplace=True)
# sweet_contacts_df.to_csv(os.path.join(dir, 'Contact.csv'), index=False, sep='\t')

# sweet_Membership_df = merge_df[ Membership_df.columns ]
# sweet_Membership_df.drop_duplicates(subset=['membershipId__c'], inplace=True)
# sweet_Membership_df.to_csv(os.path.join(dir, 'Membership__c.csv'), index=False, sep='\t')

# sweet_MTerm_df = merge_df[ MembershipTerm_df.columns ]
# sweet_MTerm_df.drop_duplicates(subset=['membershipTermId__c'], inplace=True)
# sweet_MTerm_df.to_csv(os.path.join(dir, 'MembershipTerm__c.csv'), index=False, sep='\t')

# sweet_MMember_df = merge_df[ MembershipMember_df.columns ]
# sweet_MMember_df.drop_duplicates(subset=['membershipMemberId__c'], inplace=True)
# sweet_MMember_df.to_csv(os.path.join(dir, 'MembershipMember__c.csv'), index=False, sep='\t')


In [ ]:
# # test to see if External_Id__c is unique
# sweet_contacts_df['External_Id__c'].value_counts().sort_values(ascending=False).head(10)

## Upload CSV to SF

In [ ]:
sf.execute_job(sf_object_s='Contact', operation='upsert', external_id='External_Id__c', use_ATMS_data=False)

execute_job
Created job 7508Y00000mVxrwQAC for Contact with operation upsert
Uploading job 7508Y00000mVxrwQAC of object Contact
job status: InProgress
waiting for job to complete, try 0, status: InProgress
waiting for job to complete, try 1, status: InProgress
waiting for job to complete, try 2, status: JobComplete
Failed results:
"sf__Id"	"sf__Error"	LastName	MailingPostalCode	MailingCity	MailingStreet	MailingCountry	Phone	Email	External_Id__c
""	"DUPLICATES_DETECTED:Use one of these records?:--"	"Not Provided"	"T6C 3R4"	"Edmonton"	"9237 92 st. NW"	"Canada"	" "	"harkerb@gmail.com"	"456708"
""	"DUPLICATES_DETECTED:Use one of these records?:--"	"Not Provided"	"T6V 0H9"	"Edmonton"	"536 Albany Way"	"Canada"	"7808631389"	"jzacharki@gmail.com"	"274477"
""	"DUPLICATES_DETECTED:Use one of these records?:--"	"Not Provided"	"T6V 0A5"	"Edmonton"	"14004 148 Avenue"	"Canada"	" "	"ngerbrandt@outlook.com"	"456768"
""	"DUPLICATES_DETECTED:Use one of these records?:--"	"Not Provided"	"S9V 2J8"	"Lloydm

In [ ]:
### stomping on the data ....
sf.execute_job(sf_object_s='Membership__c', operation='upsert', external_id='membershipId__c', use_ATMS_data=False)

execute_job
Created job 7508Y00000mVxskQAC for Membership__c with operation upsert
Uploading job 7508Y00000mVxskQAC of object Membership__c
job status: InProgress
Failed results:
"sf__Id"	"sf__Error"	membershipId__c	memberSince__c	updateDate__c



In [ ]:
sf.execute_job(sf_object_s='MembershipTerm__c', operation='upsert', external_id='membershipTermId__c', use_ATMS_data=False)

execute_job
Created job 7508Y00000mVxSjQAK for MembershipTerm__c with operation upsert
Uploading job 7508Y00000mVxSjQAK of object MembershipTerm__c
job status: InProgress
Failed results:
"sf__Id"	"sf__Error"	membershipTermId__c	membershipKey__r.membershipId__c	effectiveDate__c	expiryDate__c	membershipType__c	upgradeFromTermKey__c	giftMembership__c	refunded__c	saleDetailKey__c	itemKey__c



In [ ]:
sf.execute_job(sf_object_s='MembershipMember__c', operation='upsert', external_id='membershipMemberId__c', use_ATMS_data=False)

execute_job
Created job 7508Y00000mVxgRQAS for MembershipMember__c with operation upsert
Uploading job 7508Y00000mVxgRQAS of object MembershipMember__c
job status: InProgress
waiting for job to complete, try 0, status: InProgress
Failed results:
"sf__Id"	"sf__Error"	membershipMemberId__c	membershipTermKey__r.membershipTermId__c	cardNumber__c	membershipNumber__c	cardStatus__c	contactKey__r.External_Id__c	displayName__c
""	"DUPLICATE_VALUE:Duplicate external id specified: 208415.0:membershipMemberId__c --"	"208415.0"	"111063.0"	"2.0"	"5931702"	"Active"	"456287"	"Brown, Chad"
""	"DUPLICATE_VALUE:Duplicate external id specified: 208415.0:membershipMemberId__c --"	"208415.0"	"116946.0"	"2.0"	"5931702"	"Active"	"456287"	"Brown, Chad"
""	"DUPLICATE_VALUE:Duplicate external id specified: 208443.0:membershipMemberId__c --"	"208443.0"	"111072.0"	"1.0"	"5932401"	"Active"	"456309"	"Zhang, Feng"
""	"DUPLICATE_VALUE:Duplicate external id specified: 208444.0:membershipMemberId__c --"	"208444.0"	"1110

## Now we look at Salesforce site to see if the data is there...

## Try to get SF Sales data

In [ ]:

atms.retrieve_and_clean('sales', since_date='2020-01-01', max_rows=20)

download dir is:  /Users/josephmann/Documents/Github/doubledot/atms_download/enxgoj51
resp_d = self.get_telus_data(sales,offset=0, count= 20, since_date=2020-01-01)
ATMS_api.get_telus_data: since_date is 2020-01-01
http://crm-api-telus.atmsplus.com/api/sales/lastupdate?count=20&offset=0&updateDate=2020-01-01
resp_d.keys():  dict_keys(['response', 'done'])
Error retrieving data: 404
Error retrieving data: {'error': {'code': '404', 'message': 'Execution Timeout Expired.  The timeout period elapsed prior to completion of the operation or the server is not responding.', 'data': {'Not Found': 'The wait operation timed out.'}}}


ValueError: Error retrieving data: 404

## JMESPATH search stuff for Table Structure

In [ ]:
atms.obj_d['sales'][:3]

[{'saleKey': '1896116',
  'saleAmount': '0.0000',
  'paymentAmount': '0.0000',
  'saleDate': '2020-01-01T01:05:30.74',
  'active': True,
  'terminalKey': 50,
  'ticketCount': 0,
  'eventDate': None,
  'booking': {'bookingId': 0,
   'bookingContactKey': 0,
   'bookingContactType': None,
   'contactKey': 0,
   'contactIndividualKey': 0,
   'contactOrganizationKey': 0,
   'displayName': None,
   'firstName': None,
   'lastName': None,
   'email': None,
   'phone': None},
  'saleComment': None,
  'saleDetails': [],
  'tickets': []},
 {'saleKey': '1896117',
  'saleAmount': '63.8000',
  'paymentAmount': '63.8000',
  'saleDate': '2020-01-01T01:52:47.877',
  'active': True,
  'terminalKey': 50,
  'ticketCount': 2,
  'eventDate': '2020-01-04T10:30:00',
  'booking': {'bookingId': 579650,
   'bookingContactKey': 1117885,
   'bookingContactType': 'Primary                                 ',
   'contactKey': 456268,
   'contactIndividualKey': 445732,
   'contactOrganizationKey': 0,
   'displayName':

In [ ]:
jp.search('[].saleDetails', atms.obj_d['sales'])

KeyError: 'sales'

In [ ]:
"""
{'saleDetailId': 6327448,
   'saleId': 1896117,
   'itemKey': 2906,
   'scheduleKey': None,
   'rateKey': 1,
   'categoryKey': 5,
   'itemQuantity': 2,
   'pricingPriceKey': 33156,
   'itemPrice': 28.95,
   'itemTotal': 57.9,
   'couponTotal': 0.0,
   'discountTotal': 0.0,
   'total': 63.8,
   'revenueDate': '2020-01-04T10:30:00',
   'refundReasonKey': None,
   'systemPriceOverride': 'N',
   'membershipTermKey': None,
   'taxTotal': 2.9,
   'surchargeTotal': 3.0,
   'surchargeTaxTotal': 0.0,
   'pendingShiftKey': 68704,
   'pendingTerminalKey': 50,
   'pendingDateTimeStamp': '2020-01-01T01:54:50.46',
   'pendingUser': 'webuser             ',
   'finalStatus': 1,
   'finalShiftKey': 68704,
   'finalTerminalKey': 50,
   'finalDateTimeStamp': '2020-01-01T01:55:16.98',
   'finalUser': 'webuser             ',
   'refundQuantity': 0,
   'firstScheduleDetailKey': None,
   'itemDescription': 'Combo #1 - Science Centre + Marvel:  Universe of Super Heroes',
   'rateDescription': 'Public',
   'categoryDescription': 'Student',
   'scheduleDate': None}
"""

In [ ]:
jp.search('[].tickets', atms.obj_d['sales'])

[[],
 [{'ticketKey': 4064035,
   'saleKey': 1896117,
   'saleDetailKey': 6327449,
   'itemKey': 2900,
   'itemDescription': 'Marvel:  The Universe of Super Heroes',
   'itemShort': None,
   'itemType': None,
   'scheduleKey': 493542,
   'scheduleDate': '2020-01-04T10:30:00',
   'facilityKey': 0,
   'facilityDescription': None,
   'facilityShort': None,
   'ticketText': None,
   'rate': 'Public',
   'category': 'Student',
   'cancelled': None,
   'redeemed': None,
   'refunded': None,
   'isValid': False,
   'validationText': None,
   'redeemedCount': 0,
   'ticketDetailKey': 4064061,
   'scheduleDetailKey': 498048,
   'seats': 0,
   'seatsSold': 0,
   'totalTicketsScanned': 0,
   'scheduleEndDate': '2020-01-04T10:45:00',
   'ticketStatus': 'Redeemed',
   'ticketDisplay': 'TT4064035',
   'ticketSection': None,
   'ticketRow': None,
   'ticketSeat': None,
   'ticketPrefix': 'TT',
   'active': False,
   'cancelable': False,
   'contactIndividualKey': 445732,
   'individualKey': 456268,
  

In [ ]:
"""
[{'ticketKey': 4064035,
   'saleKey': 1896117,
   'saleDetailKey': 6327449,
   'itemKey': 2900,
   'itemDescription': 'Marvel:  The Universe of Super Heroes',
   'itemShort': None,
   'itemType': None,
   'scheduleKey': 493542,
   'scheduleDate': '2020-01-04T10:30:00',
   'facilityKey': 0,
   'facilityDescription': None,
   'facilityShort': None,
   'ticketText': None,
   'rate': 'Public',
   'category': 'Student',
   'cancelled': None,
   'redeemed': None,
   'refunded': None,
   'isValid': False,
   'validationText': None,
   'redeemedCount': 0,
   'ticketDetailKey': 4064061,
   'scheduleDetailKey': 498048,
   'seats': 0,
   'seatsSold': 0,
   'totalTicketsScanned': 0,
   'scheduleEndDate': '2020-01-04T10:45:00',
   'ticketStatus': 'Redeemed',
   'ticketDisplay': 'TT4064035',
   'ticketSection': None,
   'ticketRow': None,
   'ticketSeat': None,
   'ticketPrefix': 'TT',
   'active': False,
   'cancelable': False,
   'contactIndividualKey': 445732,
   'individualKey': 456268,
   'individualName': 'Aulakh, Naavneet',
   'contactOrganizationKey': None,
   'organizationKey': None,
   'organizationName': None,
   'reschedulable': False,
   'rescheduleLead': None,
   'rescheduleGrace': None,
   'rescheduleCount': None,
   'rescheduleLimitHours': None,
   'comment': None,
   'transferRequestKey': 0,
   'recipientEmail': None},
   """

In [ ]:
sf.get_sf_object_ids('MembershipMember__c')

Retrieving Object Ids for MembershipMember__c from Salesforce
total number of objects =  0


[]

In [ ]:
sf.execute_job(sf_object_s='MembershipMember__c', operation='upsert', external_id='membershipMemberId__c')

execute_job
Processing memberships data
Salesforce: Writing 200 memberships objects to /Users/josephmann/Documents/Github/doubledot/sf_download/Membership__c.csv
Salesforce: Writing 240 membership_terms objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipTerm__c.csv
Salesforce: Writing 767 membership_members objects to /Users/josephmann/Documents/Github/doubledot/sf_download/MembershipMember__c.csv
Created job 7508Y00000mVkSUQA0 for MembershipMember__c with operation upsert
Uploading job 7508Y00000mVkSUQA0 of object MembershipMember__c
job status: UploadComplete
waiting for job to complete, try 0, status: UploadComplete
waiting for job to complete, try 1, status: InProgress
waiting for job to complete, try 2, status: InProgress
waiting for job to complete, try 3, status: InProgress
waiting for job to complete, try 4, status: InProgress
Failed results:
"sf__Id"	"sf__Error"	membershipMemberId__c	membershipTermKey__r.membershipTermId__c	cardNumber__c	membershipNu

In [ ]:
contacts_df = pd.read_csv(os.path.join(Salesforce.class_download_dir, 'Contact.csv'), sep='\t')
contacts_df.head()

LastName MailingPostalCode MailingCity                 MailingStreet   
0  Not Provided           T2Z 3G1     Calgary       112 Douglas Glen Pt. SE  \
1  Not Provided                                                               
2  Not Provided           T6E 4Y8    Edmonton       1402-8920 100 Street NW   
3  Not Provided                                                               
4  Not Provided           T2Z 0P9     Calgary  35 Brightonwoods Crescent SE   

  MailingCountry       Phone                         Email  External_Id__c  
0         Canada  5872150656            naavie90@gmail.com          456268  
1                 3062882205            brcfdc@sasktel.net          456270  
2         Canada  5878790772  preetam.anbukarasu@gmail.com          366254  
3                 7808033826      evanogo.comm94@gmail.com          456271  
4         Canada  5878886555        derekhucul@hotmail.com          456272

In [ ]:
Mmembers_df = pd.read_csv(os.path.join(Salesforce.class_download_dir, 'MembershipMember__c.csv'), sep='\t')
Mmembers_df.head()

membershipMemberId__c  membershipTermKey__r.membershipTermId__c   
0                 208402                                    111055  \
1                 208403                                    111055   
2                 208404                                    111055   
3                 208406                                    111057   
4                 208407                                    111057   

   cardNumber__c  membershipNumber__c cardStatus__c   
0              1              5931301      Refunded  \
1              2              5931302      Refunded   
2              3              5931303      Refunded   
3              1              5931401        Active   
4              2              5931402        Active   

   contactKey__r.External_Id__c  displayName__c  
0                        456274   Thomas, Sarah  
1                        456275    Thomas, Alex  
2                        456276  Thomas, Annika  
3                        229230      Oh, Jeanne  
4                        229231  Higginson, Jim

In [ ]:
Mmembers_df.merge(contacts_df, left_on='contactKey__r.External_Id__c', right_on='External_Id__c', how='inner').head()

membershipMemberId__c  membershipTermKey__r.membershipTermId__c   
0                 208402                                    111055  \
1                 208403                                    111055   
2                 208404                                    111055   
3                 208406                                    111057   
4                 208407                                    111057   

   cardNumber__c  membershipNumber__c cardStatus__c   
0              1              5931301      Refunded  \
1              2              5931302      Refunded   
2              3              5931303      Refunded   
3              1              5931401        Active   
4              2              5931402        Active   

   contactKey__r.External_Id__c  displayName__c      LastName   
0                        456274   Thomas, Sarah  Not Provided  \
1                        456275    Thomas, Alex  Not Provided   
2                        456276  Thomas, Annika  Not Provided   
3                        229230      Oh, Jeanne  Not Provided   
4                        229231  Higginson, Jim  Not Provided   

  MailingPostalCode MailingCity          MailingStreet MailingCountry   
0           T4X 1C6    Beaumont         4313 54 Street         Canada  \
1           T4X 1C6    Beaumont         4313 54 Street         Canada   
2           T4X 1C6    Beaumont         4313 54 Street         Canada   
3           T6X 0H2    Edmonton  6068 Stanton Drive SW         Canada   
4           T6X 0H2    Edmonton  6068 Stanton Drive SW         Canada   

          Phone                  Email  External_Id__c  
0                morrisonsarah@live.ca          456274  
1                morrisonsarah@live.ca          456275  
2                morrisonsarah@live.ca          456276  
3  780-399-5537   joh@capitalpower.com          229230  
4  780-399-5537   joh@capitalpower.com          229231

In [ ]:
fail_df = pd.read_csv(io.StringIO(sf.failed_results().text), sep='\t' )
fail_df

sf__Id                                          sf__Error   
0       NaN  INVALID_FIELD:Foreign key external ID: 456282 ...  \
1       NaN  INVALID_FIELD:Foreign key external ID: 456286 ...   
2       NaN  DUPLICATE_VALUE:Duplicate external id specifie...   
3       NaN  INVALID_FIELD:Foreign key external ID: 456286 ...   
4       NaN  DUPLICATE_VALUE:Duplicate external id specifie...   
..      ...                                                ...   
674     NaN  INVALID_FIELD:Foreign key external ID: 457086 ...   
675     NaN  INVALID_FIELD:Foreign key external ID: 457087 ...   
676     NaN  INVALID_FIELD:Foreign key external ID: 457086 ...   
677     NaN  INVALID_FIELD:Foreign key external ID: 457087 ...   
678     NaN  INVALID_FIELD:Foreign key external ID: 457094 ...   

     membershipMemberId__c  membershipTermKey__r.membershipTermId__c   
0                 208410.0                                  111059.0  \
1                 208414.0                                  111063.0   
2                 208415.0                                  111063.0   
3                 208414.0                                  116946.0   
4                 208415.0                                  116946.0   
..                     ...                                       ...   
674               209111.0                                  111402.0   
675               209112.0                                  111402.0   
676               209111.0                                  115160.0   
677               209112.0                                  115160.0   
678               209113.0                                  111404.0   

     cardNumber__c  membershipNumber__c cardStatus__c   
0              1.0              5931501        Active  \
1              1.0              5931701        Active   
2              2.0              5931702        Active   
3              1.0              5931701        Active   
4              2.0              5931702        Active   
..             ...                  ...           ...   
674            1.0              5951801        Active   
675            2.0              5951802        Active   
676            1.0              5951801        Active   
677            2.0              5951802        Active   
678            1.0              5951901        Active   

     contactKey__r.External_Id__c    displayName__c  
0                          456282      Vela, Amelia  
1                          456286  Brown, Stephanie  
2                          456287       Brown, Chad  
3                          456286  Brown, Stephanie  
4                          456287       Brown, Chad  
..                            ...               ...  
674                        457086     Place, Janice  
675                        457087     Winer, Gordon  
676                        457086     Place, Janice  
677                        457087     Winer, Gordon  
678                        457094   Larsen, Michael  

[679 rows x 9 columns]

In [ ]:
set(fail_df.sf__Error)

{'DUPLICATE_VALUE:Duplicate external id specified: 208414.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208415.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208443.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208444.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208445.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208471.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208482.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208483.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208484.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208485.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id specified: 208519.0:membershipMemberId__c --',
 'DUPLICATE_VALUE:Duplicate external id spe

In [ ]:
# let's start with 

In [ ]:
# print(failed_response.text)
# pd.read_csv(io.StringIO(failed_response.text), sep='\t')

In [ ]:
#| hide
import nbdev; nbdev.nbdev_export()

In [ ]:
sf.bearer_token

NameError: name 'sf' is not defined

## Custom Field Addition

```C#
@RestResource(urlMapping = '/Customfields')
global class CreateCustomfields 
{
    @HttpPost
    global static Map<String,String> GenerateCustomfields(
        String fieldType,
        String ObjectName,
        boolean Required,
        integer length,
        String label,
        String description,
        String inlineHelpText) 
    {
        Map<String,String> Resp = new Map<String,String> ();
        HttpRequest request = new HttpRequest();
        request.setHeader('Authorization', 'Bearer ' + UserInfo.getSessionID());
        request.setHeader('Content-Type','application/json');
        request.setEndpoint(URL.getSalesforceBaseUrl().toExternalForm()+'/services/data/v56.0/tooling/sobjects/CustomField/');
        request.setMethod('POST');
        if(fieldType == 'Text')
        {
            request.setBody('{"Metadata" : {"type" : "'+fieldType+'","description" : "'+description+'", "inlineHelpText" : "'+inlineHelpText+'","label" : "'+label+'","length" : '+length+',"required" : '+Required+'}, "FullName" : "'+ObjectName+'.'+label.replace(' ','_')+'__c"}');
        }
        else
        {
            Resp.put('Error','Please provide field type');
            return Resp;
        }
        Http http = new Http();
        HTTPResponse res = http.send(request);	
        if(res.getStatusCode()==200 || res.getStatusCode()==201)
        {
        Resp.put('Success','status: '+res.getStatus()+' Status Code: '+res.getStatusCode());
        Resp.put('StatusCode',''+res.getStatusCode());
        Map<String, Object> m = (Map<String, Object>) JSON.deserializeUntyped(res.getBody());

            Resp.put('requestgetBody',URL.getSalesforceBaseUrl().toExternalForm()+
            '/lightning/setup/ObjectManager/'+ObjectName+
            '/FieldsAndRelationships/'+''+m.get('id')+'/view');
        }else
        {  String body=res.getBody();
            Resp.put('Error',''+res.getStatus());
            Resp.put('StatusCode',''+res.getStatusCode());
            body=body.substring( 1, body.length() - 1 );
            map<String,object> m = (map<String,object>) JSON.deserializeUntyped(body);
            Resp.put('ErrorMessage',''+m.get('message'));
            Resp.put('Endpoint',''+request.getEndpoint());
        }
        return Resp;
    }
}


```

In [ ]:
import requests
import json

url = "https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/apexrest/Customfields"

payload = json.dumps({
  "fieldType": "Text",
  "ObjectName": "Opportunity",
  "Required": False,
  "length": 255,
  "label": "Comment2",
  "description": "Comment2",
  "inlineHelpText": "Opportunity Comment"
})
headers = {
  'Content-Type': 'application/json',
  'Authorization': f'Bearer {sf._sf_access_token}',  
  'Cookie': 'BrowserId=9iqd6PLUEe2Kc5165b9Nzw; CookieConsentPolicy=0:1; LSKey-c$CookieConsentPolicy=0:1'
}

response = requests.request("POST", url, headers=headers, data=payload)

print(response.text)


{"Endpoint":"https://cremaconsulting-dev-ed.develop.my.salesforce.com/services/data/v56.0/tooling/sobjects/CustomField/","ErrorMessage":"There is already a field named Comment2 on Opportunity.","StatusCode":"400","Error":"Bad Request"}


In [ ]:
response

<Response [200]>

In [ ]:
response.json()

{'requestgetBody': 'https://cremaconsulting-dev-ed.develop.my.salesforce.com/lightning/setup/ObjectManager/Opportunity/FieldsAndRelationships/00N8Y00000MDiQCUA1/view',
 'StatusCode': '201',
 'Success': 'status: Created Status Code: 201'}